<a href="https://colab.research.google.com/github/programadormovel/13-Interface-Exemplos/blob/main/tradutor_vlibras.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install transformers[torch] datasets sentencepiece -q
!pip install sacremoses

import torch
from transformers import MarianMTModel, MarianTokenizer, Trainer, TrainingArguments

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 897.5/897.5 kB 6.8 MB/s eta 0:00:00


In [ ]:
# Carregando o modelo pré-treinado (usaremos um modelo base de PT para melhorar)
model_name = "Helsinki-NLP/opus-mt-tc-big-en-pt" # Modelo base para ajuste
tokenizer = MarianTokenizer.from_pretrained(model_name)
model = MarianMTModel.from_pretrained(model_name)

def traduzir_glosa_vibras(glosa):
    # O VLibrasBD exige que os dados entrem em caixa alta
    inputs = tokenizer(glosa.upper(), return_tensors="pt", padding=True)

    # Gerando a tradução com Beam Search (busca por melhor probabilidade)
    with torch.no_grad():
        translated_tokens = model.generate(**inputs, max_length=128)

    resultado = tokenizer.batch_decode(translated_tokens, skip_special_tokens=True)
    return resultado[0]

# Exemplo de fluxo do VLibrasBD
exemplo_vlb = "HOJE EU COMER MAÇÃ"
print(f"Entrada (VLibrasBD): {exemplo_vlb}")
print(f"Saída (Deep Learning): {traduzir_glosa_vibras(exemplo_vlb)}")

tokenizer_config.json:   0%|          | 0.00/337 [00:00<?, ?B/s]

source.spm:   0%|          | 0.00/803k [00:00<?, ?B/s]

target.spm:   0%|          | 0.00/825k [00:00<?, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/65.0 [00:00<?, ?B/s]

config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/465M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/301 [00:00<?, ?B/s]

Entrada (VLibrasBD): HOJE EU COMER MAÇÃ
Saída (Deep Learning): HOJE EU COMER MA


In [ ]:
import pandas as pd
import os
from datasets import Dataset
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, DataCollatorForSeq2Seq, Seq2SeqTrainingArguments, Seq2SeqTrainer

# 1. Carregamento dos dados (Ajustado para o arquivo que você subiu no Colab)
caminho_arquivo = "pt_br2libras_gloss.csv" # Nome do arquivo após o upload no Colab

if os.path.exists(caminho_arquivo):
    df = pd.read_csv(caminho_arquivo)
    print("Arquivo carregado. Colunas encontradas:", df.columns.tolist())
else:
    print(f"⚠️ Arquivo '{caminho_arquivo}' não encontrado.")
    print("Criando um dataset de exemplo (dummy) para demonstração do código...")
    # Cria dados fictícios para não travar o código
    df = pd.DataFrame({
        "libras-gloss": ["EU GOSTAR ESTUDAR", "HOJE DIA BOM", "NOME MEU JOAO"],
        "pt-br": ["Eu gosto de estudar", "Hoje o dia está bom", "Meu nome é João"]
    })

# 2. Configuração do Modelo (Focado em Português do Brasil)
model_checkpoint = "unicamp-dl/ptt5-small-portuguese-vocab"
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)
model = AutoModelForSeq2SeqLM.from_pretrained(model_checkpoint)

def preprocess_function(examples):
    # Ajuste 'gloss' e 'text' para o nome exato das colunas do seu CSV
    # No VLibrasBD, a glosa é a entrada (input) e o texto é o alvo (target)
    inputs = ["traduzir glosa: " + str(doc) for doc in examples["libras-gloss"]]
    model_inputs = tokenizer(inputs, max_length=128, truncation=True, padding="max_length")

    # Correção: usar text_target em vez de as_target_tokenizer()
    labels = tokenizer(text_target=examples["pt-br"], max_length=128, truncation=True, padding="max_length")

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

# Converter DataFrame para Dataset do Hugging Face
dataset = Dataset.from_pandas(df.dropna())
tokenized_dataset = dataset.map(preprocess_function, batched=True)

# 3. Parâmetros de Treinamento para o Mestrado
training_args = Seq2SeqTrainingArguments(
    output_dir="./resultados_vlibras",
    eval_strategy="no", # Alterado de evaluation_strategy para eval_strategy
    learning_rate=5e-5,
    per_device_train_batch_size=16,
    weight_decay=0.01,
    save_total_limit=2,
    num_train_epochs=30, # Reduzido para 3 épocas para um teste mais rápido
    predict_with_generate=True,
    fp16=True,
)

# Criação explícita do Data Collator
data_collator = DataCollatorForSeq2Seq(tokenizer, model=model)

trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset,
    data_collator=data_collator,
    # tokenizer=tokenizer, # Removido para evitar erro de argumento inesperado no __init__
)

# Atribuir tokenizer manualmente para garantir funcionamento do predict_with_generate
trainer.tokenizer = tokenizer

# Iniciar o Fine-Tuning
trainer.train()

Arquivo carregado. Colunas encontradas: ['pt-br', 'libras-gloss', 'is_government_source', 'english_translation']


Loading weights:   0%|          | 0/133 [00:00<?, ?it/s]

The tied weights mapping and config for this model specifies to tie shared.weight to encoder.embed_tokens.weight, but both are present in the checkpoints, so we will NOT tie them. You should update the config with `tie_word_embeddings=False` to silence this warning
The tied weights mapping and config for this model specifies to tie shared.weight to decoder.embed_tokens.weight, but both are present in the checkpoints, so we will NOT tie them. You should update the config with `tie_word_embeddings=False` to silence this warning


Map:   0%|          | 0/127349 [00:00<?, ? examples/s]

Writing model shards:   0%|          | 0/1 [00:00<?, ?it/s]

...

Writing model shards:   0%|          | 0/1 [00:00<?, ?it/s]

Writing model shards:   0%|          | 0/1 [00:00<?, ?it/s]

Writing model shards:   0%|          | 0/1 [00:00<?, ?it/s]

Writing model shards:   0%|          | 0/1 [00:00<?, ?it/s]

TrainOutput(global_step=238800, training_loss=0.29606927271065003, metrics={'train_runtime': 36956.8238, 'train_samples_per_second': 103.377, 'train_steps_per_second': 6.462, 'total_flos': 1.2926732306743296e+17, 'train_loss': 0.29606927271065003, 'epoch': 30.0})

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

# Carrega o tokenizador e modelo se não estiverem definidos
try:
    tokenizer
    model
except NameError:
    print("Carregando modelo e tokenizador (base)...")
    model_checkpoint = "unicamp-dl/ptt5-small-portuguese-vocab"
    tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)
    model = AutoModelForSeq2SeqLM.from_pretrained(model_checkpoint)

def traduzir_vlb_final(glosa):
    input_text = "traduzir glosa: " + glosa.upper()
    device = "cuda" if torch.cuda.is_available() else "cpu"

    model.to(device)
    inputs = tokenizer(input_text, return_tensors="pt").input_ids.to(device)

    outputs = model.generate(inputs, max_length=128, num_beams=5, early_stopping=True)
    return tokenizer.decode(outputs[0], skip_special_tokens=True)

# Teste com uma frase do conjunto de treino (Dummy) e uma nova
print("--- Teste com frase conhecida (Treino Dummy) ---")
print(f"Entrada: EU GOSTAR ESTUDAR")
print(f"Saída:   {traduzir_vlb_final('EU GOSTAR ESTUDAR')}")

print("\n--- Teste com frase nova (Generalização) ---")
print(f"Entrada: EU IR TRABALHAR AMANHÃ")
print(f"Saída:   {traduzir_vlb_final('EU IR TRABALHAR AMANHÃ')}")

print("\n--- Teste com frase nova (Generalização) ---")
print(f"Entrada: EU FALAR INGLÊS")
print(f"Saída:   {traduzir_vlb_final('EU FALAR INGLÊS')}")

print("\n--- Teste com frase nova (Treino Dummy) ---")
print(f"Entrada: VOCÊ NÃO_TER [INTERROGAÇÃO]")
print(f"Saída:   {traduzir_vlb_final('VOCÊ NÃO_TER [INTERROGAÇÃO]')}")

print("\n--- Teste com frase nova (Generalização) ---")
print(f"Entrada: PÚBLICO&PESSOA USUÁRIO LATINDEX TODO UTILIZAR INTERCÂMBIO GERAR&PRODUZIR INFORMAÇÃO CIENTÍFICA [PONTO]")
print(f"Saída:   {traduzir_vlb_final('PÚBLICO&PESSOA USUÁRIO LATINDEX TODO UTILIZAR INTERCÂMBIO GERAR&PRODUZIR INFORMAÇÃO CIENTÍFICA [PONTO]')}")



--- Teste com frase conhecida (Treino Dummy) ---
Entrada: EU GOSTAR ESTUDAR
Saída:   Eu gosto de estudar

--- Teste com frase nova (Generalização) ---
Entrada: EU IR TRABALHAR AMANHÃ
Saída:   Eu irei trabalhar amanhã

--- Teste com frase nova (Generalização) ---
Entrada: EU FALAR INGLÊS
Saída:   Eu falo inglês

--- Teste com frase nova (Treino Dummy) ---
Entrada: VOCÊ NÃO_TER [INTERROGAÇÃO]
Saída:   Você não tem?

--- Teste com frase nova (Generalização) ---
Entrada: PÚBLICO&PESSOA USUÁRIO LATINDEX TODO UTILIZAR INTERCÂMBIO GERAR&PRODUZIR INFORMAÇÃO CIENTÍFICA [PONTO]
Saída:   Para o público, o usuário do LATDEX todos os quais utilizam o interâmbio para gerar informações científicas.
